In [1]:
import pandas as pd
import numpy as np
import re
import matplotlib.pyplot as plt
import seaborn as sns
import geopandas as gpd
from geopy.geocoders import Nominatim
from shapely.geometry import Point, Polygon

In [2]:
postmates_lowerManhattan = pd.read_csv('/Users/baileyrusso/PycharmProjects/GrubHubScraper/test7.csv',header=None)
postmates_lowerManhattan.columns = ['Name', 'Category', 'Favorites', 'Address', 'MenuItem', 'MenuItemDescription','MenuItemPrice']

postmates_midtown = pd.read_csv('/Users/baileyrusso/PycharmProjects/GrubHubScraper/test8.csv',header=None)
postmates_midtown.columns = ['Name', 'Category', 'Favorites', 'Address', 'MenuItem', 'MenuItemDescription','MenuItemPrice']

postmates_chelsea = pd.read_csv('/Users/baileyrusso/PycharmProjects/GrubHubScraper/test9.csv',header=None)
postmates_chelsea.columns = ['Name', 'Category', 'Favorites', 'Address', 'MenuItem', 'MenuItemDescription','MenuItemPrice']
for col in postmates_chelsea.columns:
    postmates_chelsea[col] = list(map(lambda row: str(row).replace('b\'','').replace('\'','').rstrip().replace('\'','') if row != "b''" else np.nan, postmates_chelsea[col]))

postmates_NYU = pd.read_csv('/Users/baileyrusso/PycharmProjects/GrubHubScraper/test10.csv',header=None)
postmates_NYU.columns = ['Name', 'Category', 'Favorites', 'Address', 'MenuItem', 'MenuItemDescription','MenuItemPrice']
for col in postmates_NYU.columns:
    postmates_NYU[col] = list(map(lambda row: str(row).replace('b\'','').replace('\'','').rstrip().replace('\'','') if row != "b''" else np.nan, postmates_NYU[col]))
    
postmates_UWS = pd.read_csv('/Users/baileyrusso/PycharmProjects/GrubHubScraper/test11.csv',header=None)
postmates_UWS.columns = ['Name', 'Category', 'Favorites', 'Address', 'MenuItem', 'MenuItemDescription','MenuItemPrice']
for col in postmates_UWS.columns:
    postmates_UWS[col] = list(map(lambda row: str(row).replace('b\'','').replace('\'','').rstrip().replace('\'','') if row != "b''" else np.nan, postmates_UWS[col]))
    
postmates_UES = pd.read_csv('/Users/baileyrusso/PycharmProjects/GrubHubScraper/test12.csv',header=None)
postmates_UES.columns = ['Name', 'Category', 'Favorites', 'Address', 'MenuItem', 'MenuItemDescription','MenuItemPrice']
for col in postmates_UES.columns:
    postmates_UES[col] = list(map(lambda row: str(row).replace('b\'','').replace('\'','').rstrip().replace('\'','') if row != "b''" else np.nan, postmates_UES[col]))
    
    
postmates_LincolnSquare = pd.read_csv('/Users/baileyrusso/PycharmProjects/GrubHubScraper/test13.csv',header=None)
postmates_LincolnSquare.columns = ['Name', 'Category', 'Favorites', 'Address', 'MenuItem', 'MenuItemDescription','MenuItemPrice']
for col in postmates_LincolnSquare.columns:
    postmates_LincolnSquare[col] = list(map(lambda row: str(row).replace('b\'','').replace('\'','').rstrip().replace('\'','') if row != "b''" else np.nan, postmates_LincolnSquare[col]))


# Clean Address Column

In [3]:
def cleanAddressCol(df):
    addressList = []
    for i in range(len(df.Address)):
        address = df.Address.iloc[i]
        if pd.notnull(address):
            try:
                addressList.append(address.split('\n')[1].replace('(','').replace(')','').rstrip())
            except:
                print('Exception Occured: Make sure col lengths match')
                addressList.append(address.split('\\n')[1].replace('(','').replace(')','').rstrip())
        else:
            addressList.append(np.nan)

    df.Address = addressList
    print('Clean Address - Done')

# Clean Favorites Column

In [4]:
def cleanFavoritesCol(df):
    df['Favorites'] = list(map(lambda row: str(row).replace('added to favorites', '').rstrip(), df['Favorites']))
    df['Favorites'] = list(map(lambda row: str(row).replace('k', '00').replace('.','') if pd.notnull(row) else row, df['Favorites']))
    df['Favorites'] = df['Favorites'].astype(float)
    df['Favorites'] = df['Favorites'].fillna(0)
    print('Clean Favorites - Done')

# Clean Menu Item Price Column

In [5]:
def cleanMenuItemPriceCol(df):
    df['MenuItemPrice'] = [list(
        map(lambda row: float(str(row).replace('$', '').replace(',', '')) if pd.notnull(row) else row,
            df['MenuItemPrice']))][0]
    print('Clean Menu Item Price - Done')       

# Get Address Coordinates

In [6]:
def getAddressCoords(df):
    geolocator = Nominatim(user_agent= 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/90.0.4430.93 Safari/537.36')
    address_list = list(df.groupby(['Name','Address']).mean().reset_index()['Address'])
    address_coords = []

    i = 0
    for address in address_list:
        try:
            print(i)
            i = i + 1
            print(geolocator.geocode(address + str(', NYC,NY'))[1])
            address_coords.append(tuple(geolocator.geocode(address + str(', NYC,NY'))[1]))
        except:
            address_coords.append(np.nan)
            continue

    d = {'Address': address_list, 'Address_Coordinates': address_coords}
    addressInfo = pd.DataFrame(d)
    
    return addressInfo
    '''
    df = pd.merge(df, addressInfo, on='Address')

    df['Address_Coordinates'] = list(map(lambda row: str(row).replace("(", "").replace(")", "").split(","), df['Address_Coordinates']))
    df['Address_Coordinates'] = list(map(lambda row: tuple([float(i) for i in row if pd.notnull(i)]), df['Address_Coordinates']))
    df[['Latitude', 'Longitude']] = pd.DataFrame(df['Address_Coordinates'].tolist(),index=df.index)
    print('Get Address Coords - Done')
    '''



In [7]:
cleanAddressCol(postmates_lowerManhattan)
cleanFavoritesCol(postmates_lowerManhattan)
cleanMenuItemPriceCol(postmates_lowerManhattan)
addressInfo = getAddressCoords(postmates_lowerManhattan)

postmates_lowerManhattan = pd.merge(postmates_lowerManhattan, addressInfo, on='Address')
postmates_lowerManhattan['Address_Coordinates'] = list(map(lambda row: str(row).replace("(", "").replace(")", "").split(","), postmates_lowerManhattan['Address_Coordinates']))
postmates_lowerManhattan['Address_Coordinates'] = list(map(lambda row: tuple([float(i) for i in row if pd.notnull(i)]), postmates_lowerManhattan['Address_Coordinates']))
postmates_lowerManhattan[['Latitude', 'Longitude']] = pd.DataFrame(postmates_lowerManhattan['Address_Coordinates'].tolist(),index=postmates_lowerManhattan.index)
print('Get Address Coords - Done')

cleanAddressCol(postmates_midtown)
cleanFavoritesCol(postmates_midtown)
cleanMenuItemPriceCol(postmates_midtown)
addressInfo = getAddressCoords(postmates_midtown)

postmates_midtown = pd.merge(postmates_midtown, addressInfo, on='Address')
postmates_midtown['Address_Coordinates'] = list(map(lambda row: str(row).replace("(", "").replace(")", "").split(","), postmates_midtown['Address_Coordinates']))
postmates_midtown['Address_Coordinates'] = list(map(lambda row: tuple([float(i) for i in row if pd.notnull(i)]), postmates_midtown['Address_Coordinates']))
postmates_midtown[['Latitude', 'Longitude']] = pd.DataFrame(postmates_midtown['Address_Coordinates'].tolist(),index=postmates_midtown.index)
print('Get Address Coords - Done')

cleanAddressCol(postmates_chelsea)
cleanFavoritesCol(postmates_chelsea)
cleanMenuItemPriceCol(postmates_chelsea)
addressInfo = getAddressCoords(postmates_chelsea)

postmates_chelsea = pd.merge(postmates_chelsea, addressInfo, on='Address')
postmates_chelsea['Address_Coordinates'] = list(map(lambda row: str(row).replace("(", "").replace(")", "").split(","), postmates_chelsea['Address_Coordinates']))
postmates_chelsea['Address_Coordinates'] = list(map(lambda row: tuple([float(i) for i in row if pd.notnull(i)]), postmates_chelsea['Address_Coordinates']))
postmates_chelsea[['Latitude', 'Longitude']] = pd.DataFrame(postmates_chelsea['Address_Coordinates'].tolist(),index=postmates_chelsea.index)
print('Get Address Coords - Done')


cleanAddressCol(postmates_NYU)
cleanFavoritesCol(postmates_NYU)
cleanMenuItemPriceCol(postmates_NYU)
addressInfo = getAddressCoords(postmates_NYU)

postmates_NYU = pd.merge(postmates_NYU, addressInfo, on='Address')
postmates_NYU['Address_Coordinates'] = list(map(lambda row: str(row).replace("(", "").replace(")", "").split(","), postmates_NYU['Address_Coordinates']))
postmates_NYU['Address_Coordinates'] = list(map(lambda row: tuple([float(i) for i in row if pd.notnull(i)]), postmates_NYU['Address_Coordinates']))
postmates_NYU[['Latitude', 'Longitude']] = pd.DataFrame(postmates_NYU['Address_Coordinates'].tolist(),index=postmates_NYU.index)
print('Get Address Coords - Done')

cleanAddressCol(postmates_UWS)
cleanFavoritesCol(postmates_UWS)
cleanMenuItemPriceCol(postmates_UWS)
addressInfo = getAddressCoords(postmates_UWS)

postmates_UWS = pd.merge(postmates_UWS, addressInfo, on='Address')
postmates_UWS['Address_Coordinates'] = list(map(lambda row: str(row).replace("(", "").replace(")", "").split(","), postmates_UWS['Address_Coordinates']))
postmates_UWS['Address_Coordinates'] = list(map(lambda row: tuple([float(i) for i in row if pd.notnull(i)]), postmates_UWS['Address_Coordinates']))
postmates_UWS[['Latitude', 'Longitude']] = pd.DataFrame(postmates_UWS['Address_Coordinates'].tolist(),index=postmates_UWS.index)
print('Get Address Coords - Done')


Clean Address - Done
Clean Favorites - Done
Clean Menu Item Price - Done
0
(40.7133082, -74.0080416)
1
(40.7047017, -74.0088567)
2
(40.7137186, -73.998778)
3
(40.715801, -73.9992469)
4
(40.7214812, -74.0013728)
5
(40.7163736, -73.9999049)
6
(40.7218498, -73.9971334)
7
(40.7097615, -74.0088919)
8
(40.7048612, -74.0095599)
9
(40.7097449, -74.0070195)
10
(40.71950495, -74.00409816786006)
11
(40.722171349999996, -73.99636760810697)
12
(40.7207158, -73.9947851)
13
(40.7300122, -74.00283299273195)
14
(40.72210135, -73.99766773251471)
15
(40.723624349999994, -73.97893769999999)
16
(40.70343895, -74.01108522118858)
17
(40.721206, -73.996278)
18
(40.7149438, -74.01086851127356)
19
(40.7048612, -74.0095599)
20
(40.7166208, -73.9997625)
21
(40.7186316, -73.9893489)
22
(40.716357, -73.9991738)
23
(40.713865, -73.9987984)
24
(40.709584199999995, -74.007034739265)
25
(40.707665750000004, -74.00595246337208)
26
(40.7215851, -73.9972327)
27
(40.7113535, -73.9998293)
28
(40.7048612, -74.0095599)
29
(40

84
(40.7549721, -73.9655837)
85
(40.7441181, -73.9952986)
86
(40.7627719, -73.9966632)
87
(40.6994582, -73.9921983)
88
(40.7627719, -73.9966632)
89
(40.7549721, -73.9655837)
90
(40.7549721, -73.9655837)
91
(40.65874844444444, -74.00589496296297)
92
(40.7638948, -73.9921449)
93
(40.7640651, -73.9670374)
94
(40.7640822, -73.9887421)
95
(40.72589, -74.0092948)
96
(40.755742850000004, -73.99654634999999)
97
(40.7606764, -73.997433)
98
(40.7627719, -73.9966632)
99
(40.7549721, -73.9655837)
100
(40.7588045, -73.99648829750845)
101
(40.7583497, -73.9831961757719)
102
(40.65987526530612, -73.99836302040816)
103
(40.7640822, -73.9887421)
104
(40.75945325, -73.96906294833789)
105
(40.75334205, -73.97397388850807)
106
(40.7388452, -73.9998143)
107
(40.75945325, -73.96906294833789)
108
109
(40.7549721, -73.9655837)
110
(40.75945325, -73.96906294833789)
111
(40.760457375, -73.97614854166667)
112
(40.7642764, -73.99170635)
113
(40.7588045, -73.99648829750845)
114
(40.75945325, -73.96906294833789)
11

Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occ

Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occ

Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occ

...

Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occ

Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occ

Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occ

Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occ

Clean Favorites - Done
Clean Menu Item Price - Done
0
(40.7806573, -73.9798764)
1
(40.79932, -73.9687902)
2
(40.7986655, -73.96292120478324)
3
(40.783782, -73.97820819768367)
4
(40.7857695, -73.9761873)
5
6
(40.7955955, -73.9707504)
7
(40.7930423, -73.9713664)
8
(40.767928100000006, -73.9685622225085)
9
(40.7835276, -73.97782)
10
(40.794320549999995, -73.96598023852205)
11
(40.7836802, -73.9781663)
12
(40.7867051, -73.9760764442878)
13
(40.63579984375, -74.0337819375)
14
(40.7781074, -73.9853594)
15
(40.7902348, -73.9727412)
16
(40.62901518367347, -74.03124455102041)
17
(40.7853916, -73.9727142)
18
(40.7931896, -73.9713553995)
19
(40.7446682, -73.98756)
20
(40.808856, -73.930131)
21
(40.7905139, -73.9456581)
22
(40.7683165, -73.9856517)
23
(40.785904200000004, -73.9759618587037)
24
(40.7880383, -73.9763608)
25
(40.7794271, -73.98292984316242)
26
(40.8996615, -73.8971489)
27
(40.7723547, -73.9570678)
28
(40.626847, -74.035392)
29
(40.7867051, -73.9760764442878)
30
(40.7972108, -73.96958

In [8]:
cleanAddressCol(postmates_UES)
cleanFavoritesCol(postmates_UES)
cleanMenuItemPriceCol(postmates_UES)
addressInfo = getAddressCoords(postmates_UES)

postmates_UES = pd.merge(postmates_UES, addressInfo, on='Address')
postmates_UES['Address_Coordinates'] = list(map(lambda row: str(row).replace("(", "").replace(")", "").split(","), postmates_UES['Address_Coordinates']))
postmates_UES['Address_Coordinates'] = list(map(lambda row: tuple([float(i) for i in row if pd.notnull(i)]), postmates_UES['Address_Coordinates']))
postmates_UES[['Latitude', 'Longitude']] = pd.DataFrame(postmates_UES['Address_Coordinates'].tolist(),index=postmates_UES.index)
print('Get Address Coords - Done')

Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occ

Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occ

Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occ

Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occ

Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occ

Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occ

(40.7762933, -73.9555644)
1
(40.7640414, -73.9850873)
2
(40.76618795, -73.99411114134588)
3
(40.7985915, -73.9415679)
4
(40.8105914, -73.952947)
5
(40.7785223, -73.9822861)
6
(40.762526, -73.9856926)
7
(40.758199250000004, -73.9664048)
8
(40.76493705, -73.98167833520408)
9
(40.7794306, -73.9773404)
10
(40.774351100000004, -73.95088375825574)
11
(40.777497499999996, -73.98217149999999)
12
(40.7759935, -73.9468405)
13
(40.7797881, -73.9505975)
14
(40.7742803, -73.94799542335639)
15
(40.6994582, -73.9921983)
16
(40.7793062, -73.9808976)
17
(40.7640822, -73.9887421)
18
(40.7671015, -73.9939586)
19
(40.7588045, -73.99648829750845)
20
(40.7762451, -73.9524595339416)
21
(40.762526, -73.9856926)
22
(40.7972011, -73.9386694)
23
(40.7642764, -73.99170635)
24
(40.7642764, -73.99170635)
25
(40.7292263, -73.9869976)
26
(40.7880437, -73.94171690969463)
27
(40.7642764, -73.99170635)
28
(40.74103555, -73.99370340745092)
29
(40.7439385, -73.9997311)
30
(40.7659, -73.9571707)
31
(40.7778959, -73.9825105

In [9]:
cleanAddressCol(postmates_LincolnSquare)
cleanFavoritesCol(postmates_LincolnSquare)
cleanMenuItemPriceCol(postmates_LincolnSquare)
addressInfo = getAddressCoords(postmates_LincolnSquare)

postmates_LincolnSquare = pd.merge(postmates_LincolnSquare, addressInfo, on='Address')
postmates_LincolnSquare['Address_Coordinates'] = list(map(lambda row: str(row).replace("(", "").replace(")", "").split(","), postmates_LincolnSquare['Address_Coordinates']))
postmates_LincolnSquare['Address_Coordinates'] = list(map(lambda row: tuple([float(i) for i in row if pd.notnull(i)]), postmates_LincolnSquare['Address_Coordinates']))
postmates_LincolnSquare[['Latitude', 'Longitude']] = pd.DataFrame(postmates_LincolnSquare['Address_Coordinates'].tolist(),index=postmates_LincolnSquare.index)
print('Get Address Coords - Done')

Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occ

Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occ

Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occ

Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occ

Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occ

Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occ

Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occured: Make sure col lengths match
Exception Occ

(40.762979, -73.9932511)
1
(40.7628307, -73.9896418)
2
(40.7640414, -73.9850873)
3
(40.76457185, -73.98850785276343)
4
(40.7627719, -73.9966632)
5
(40.7321893, -74.0034001)
6
(40.7627719, -73.9966632)
7
(40.7579095, -73.9909024)
8
(40.8105914, -73.952947)
9
(40.7627719, -73.9966632)
10
(40.7627719, -73.9966632)
11
(40.7586023, -73.9660296)
12
(40.7785223, -73.9822861)
13
(40.757554, -73.989917)
14
(40.7831271, -73.9808114)
15
(40.762526, -73.9856926)
16
(40.758199250000004, -73.9664048)
17
(40.7794306, -73.9773404)
18
(40.7603776, -73.9851653)
19
(40.7626429, -73.9899518046432)
20
(40.777497499999996, -73.98217149999999)
21
(40.7640822, -73.9887421)
22
(40.7797881, -73.9505975)
23
(40.7627719, -73.9966632)
24
(40.6994582, -73.9921983)
25
(40.7627719, -73.9966632)
26
(40.7793062, -73.9808976)
27
(40.7638948, -73.9921449)
28
(40.7640822, -73.9887421)
29
(40.7671015, -73.9939586)
30
(40.7588045, -73.99648829750845)
31
(40.762526, -73.9856926)
32
(40.7972011, -73.9386694)
33
(40.7981781, -

In [10]:
postmates = pd.concat([postmates_lowerManhattan, postmates_midtown, postmates_chelsea, postmates_NYU, postmates_UWS])
postmates.columns = ['Name', 'Category', 'Favorites', 'Address', 'MenuItem', 'MenuItemDescription', 'MenuItemPrice', 'Address_Coordinates','Latitude','Longitude']



In [11]:
postmates

Name   Category  Favorites             Address  \
0      Bluestone Lane Cafe  BREAKFAST       52.0       19 KENMARE ST   
1      Bluestone Lane Cafe  BREAKFAST       52.0       19 KENMARE ST   
2      Bluestone Lane Cafe  BREAKFAST       52.0       19 KENMARE ST   
3      Bluestone Lane Cafe  BREAKFAST       52.0       19 KENMARE ST   
4      Bluestone Lane Cafe  BREAKFAST       52.0       19 KENMARE ST   
...                    ...        ...        ...                 ...   
24308  Piccolo Caf\xc3\xa9    ITALIAN        0.0  313 AMSTERDAM AVE.   
24309  Piccolo Caf\xc3\xa9    ITALIAN        0.0  313 AMSTERDAM AVE.   
24310  Piccolo Caf\xc3\xa9    ITALIAN        0.0  313 AMSTERDAM AVE.   
24311  Piccolo Caf\xc3\xa9    ITALIAN        0.0  313 AMSTERDAM AVE.   
24312  Piccolo Caf\xc3\xa9    ITALIAN        0.0  313 AMSTERDAM AVE.   

                                              MenuItem  \
0                                       BL Burrito (D)   
1                                       BL Burrito (D)   
2                                    Avocado Smash (D)   
3                                    Avocado Smash (D)   
4                                           Iced Latte   
...                                                ...   
24308  Paccheri with Artichoke, Truffle & Bufala Pasta   
24309                  Paccheri alla Amatriciana Pasta   
24310             Paccheri & Eggplant Alla Norma Pasta   
24311                    Prosciutto, Salame and Cheese   
24312                                         Tiramisu   

                                     MenuItemDescription  MenuItemPrice  \
0      Scrambled eggs, bacon, avocado, feta, crispy p...           15.4   
1      Scrambled eggs, bacon, avocado, feta, crispy p...           15.4   
2      Our classic avo smash with feta, heirloom toma...           14.3   
3      Our classic avo smash with feta, heirloom toma...           14.3   
4      Double shot of our signature maverick espresso...            NaN   
...                                                  ...            ...   
24308  Truffle and artichoke sauce with fresh mozzare...           20.0   
24309          Penne with pecorino Romano and guanciale.           19.0   
24310  A classic Sicilian dish, fresh ricotta and egg...           19.0   
24311  Assorted imported Italian cheeses and cured me...           25.0   
24312                                                NaN           12.0   

             Address_Coordinates   Latitude  Longitude  
0      (40.7207158, -73.9947851)  40.720716 -73.994785  
1      (40.7207158, -73.9947851)  40.720716 -73.994785  
2      (40.7207158, -73.9947851)  40.720716 -73.994785  
3      (40.7207158, -73.9947851)  40.720716 -73.994785  
4      (40.7207158, -73.9947851)  40.720716 -73.994785  
...                          ...        ...        ...  
24308                     (nan,)        NaN        NaN  
24309                     (nan,)        NaN        NaN  
24310                     (nan,)        NaN        NaN  
24311                     (nan,)        NaN        NaN  
24312                     (nan,)        NaN        NaN  

[199427 rows x 10 columns]

In [12]:
postmates = postmates.drop_duplicates(subset=['Name','MenuItem','MenuItemDescription','Address_Coordinates'], keep='first')

In [13]:
postmates.to_csv('postmates_all6.csv')

In [14]:
len(postmates.groupby(['Name', 'Category', 'Latitude', 'Longitude']).mean())

662